<a href="https://colab.research.google.com/github/post-writer/tortoise-tts/blob/main/tortoise_tts.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Welcome to Tortoise! 🐢🐢🐢🐢

Before you begin, I **strongly** recommend you turn on a GPU runtime.

There's a reason this is called "Tortoise" - this model takes up to a minute to perform inference for a single sentence on a GPU. Expect waits on the order of hours on a CPU.

In [1]:
from IPython.core.display import publish_display_data
import os
if os.path.isdir('/content/tortoise-tts/tortoise-tts'):
  os.system("rm -rf /content/tortoise-tts/tortoise-tts")

if os.path.isdir('/content/tortoise-tts'):
  %cd "/content/tortoise-tts"
  os.system("git pull")
else:
  %cd "/content/"
  os.system("git clone https://github.com/post-writer/tortoise-tts.git")
%cd '/content/tortoise-tts'
!pip3 install -r "/content/tortoise-tts/requirements.txt"
%cd '/content/tortoise-tts'
!python3 setup.py install

/content
/content/tortoise-tts
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 4.4 MB 5.3 MB/s 
     |████████████████████████████████| 6.6 MB 50.6 MB/s 
     |████████████████████████████████| 235 kB 66.5 MB/s 
     |████████████████████████████████| 3.5 MB 27.0 MB/s 
     |████████████████████████████████| 20.2 MB 7.9 MB/s 
     |████████████████████████████████| 101 kB 14.7 MB/s 
     |████████████████████████████████| 596 kB 72.1 MB/s 
  Created wheel for progressbar: filename=progressbar-2.5-py3-none-any.whl size=12082 sha256=2c3757071dab8619cfb327b87c2a9f7047cc628701bae31f1e73ec531edbd0c6
  Stored in directory: /root/.cache/pip/wheels/f0/fd/1f/3e35ed57e94cd8ced38dd46771f1f0f94f65fec548659ed855
  Created wheel for ffmpeg: filename=ffmpeg-1.4-py3-none-any.whl size=6084 sha256=4546dc33b8066d1cbd0a5f8cd5b392b068806db81cfa02276cae88802d68a31d
  Stored in directory: /root/.cache/pip/wheels/64/80/

In [ ]:
import IPython

from tortoise.api import TextToSpeech
from tortoise.utils.audio import load_audio, load_voice, load_voices

# Tortoise comes with some scripts that does a lot of the lifting for you. For example,
# read.py will read a text file for you.
voice="mk"
preset="high_quality"
!python3 tortoise/read.py --voice={voice} --textfile=text_to_read.txt --preset={preset} --output_path=.

#os.system(cmd)

IPython.display.Audio(f"{voice}/combined.wav")
# This will take awhile..



Generating autoregressive samples..
100% 16/16 [01:22<00:00,  5.17s/it]
Computing best candidates using CLVP
  0% 0/16 [00:00<?, ?it/s]/usr/local/lib/python3.7/dist-packages/torch/utils/checkpoint.py:25: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn("None of the inputs have requires_grad=True. Gradients will be None")
100% 16/16 [00:17<00:00,  1.07s/it]
Transforming autoregressive outputs into audio..
100% 400/400 [00:48<00:00,  8.25it/s]


In [ ]:
# Imports used through the rest of the notebook.
import torch
import torchaudio
import torch.nn as nn
import torch.nn.functional as F

import IPython

from tortoise.api import TextToSpeech
from tortoise.utils.audio import load_audio, load_voice, load_voices

# This will download all the models used by Tortoise from the HF hub.
tts = TextToSpeech()

ModuleNotFoundError: ignored

In [ ]:
# Tortoise will attempt to mimic voices you provide. It comes pre-packaged
# with some voices you might recognize.

# Let's list all the voices available. These are just some random clips I've gathered
# from the internet as well as a few voices from the training dataset.
# Feel free to add your own clips to the voices/ folder.

%ls **/*.wav

IPython.display.Audio('tortoise/voices/mk/1.wav')

angie/                freeman/   myself/   tim_reynolds/   train_lescault/
applejack/            geralt/    nilbog/   tom/            train_mouse/
balthazar/            gribbles/  otw/      train_atkins/   weaver/
cassandra/            halle/     pat/      train_daws/     william/
chihuahua/            jlaw/      pat2/     train_dotrice/  yeepo/
cond_latent_example/  lj/        pumpkin/  train_dreams/
daniel/               mk/        rainbow/  train_empire/
deniro/               mol/       scot/     train_grace/
emma/                 movie/     snakes/   train_kennard/


In [ ]:
# This is the text that will be spoken.
texts = [ "kermit say not easy be green",
"dog not know which gray that is",
"miss big he he little green hue",
"mend pups and plays banjo yups",
"to gather derple brain pros",
"dog pair his song to heart",
"suppose he what on other side",
"making even refrain glow"] 


# Pick one of the voices from the output above
voice = 'nilbog'

# Pick a "preset mode" to determine quality. Options: {"ultra_fast", "fast" (default), "standard", "high_quality"}. See docs in api.py
preset = "high_quality"

# Load it and send it through Tortoise.
voice_samples, conditioning_latents = load_voice(voice)
for idx, text in enumerate(texts): 
  gen = tts.tts_with_preset(text, voice_samples=voice_samples, conditioning_latents=conditioning_latents, 
                          preset=preset)
  filename=f"text_{voice}_{idx}.wav"
  torchaudio.save(filename, gen.squeeze(0).cpu(), 24000)
  
  IPython.display.Audio(filename)


Generating autoregressive samples..


 19%|█▉        | 3/16 [00:08<00:36,  2.77s/it]


KeyboardInterrupt: ignored

In [ ]:
# Tortoise can also generate speech using a random voice. The voice changes each time you execute this!
# (Note: random voices can be prone to strange utterances)
gen = tts.tts_with_preset(text, voice_samples=None, conditioning_latents=None, preset=preset)
torchaudio.save('generated.wav', gen.squeeze(0).cpu(), 24000)
IPython.display.Audio('generated.wav')

Generating autoregressive samples..


100%|██████████| 16/16 [03:48<00:00, 14.27s/it]


Computing best candidates using CLVP and CVVP


  0%|          | 0/16 [00:00<?, ?it/s]/usr/local/lib/python3.7/dist-packages/torch/utils/checkpoint.py:25: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn("None of the inputs have requires_grad=True. Gradients will be None")
 94%|█████████▍| 15/16 [00:17<00:01,  1.20s/it]

No stop tokens found in one of the generated voice clips. This typically means the spoken audio is too long. In some cases, the output will still be good, though. Listen to it and if it is missing words, try breaking up your input text.


100%|██████████| 16/16 [00:18<00:00,  1.16s/it]


Transforming autoregressive outputs into audio..


100%|██████████| 200/200 [04:23<00:00,  1.32s/it]


# You can also combine conditioning voices. Combining voices produces a new voice
# with traits from all the parents.
#
# Lets see what it would sound like if Picard and Kirk had a kid with a penchant for philosophy:
voice_samples, conditioning_latents = load_voices(['pat', 'william'])

gen = tts.tts_with_preset("They used to say that if man was meant to fly, he’d have wings. But he did fly. He discovered he had to.", 
                          preset=preset)
torchaudio.save('captain_kirkard.wav', gen.squeeze(0).cpu(), 24000)
IPython.display.Audio('captain_kirkard.wav')

In [ ]:
del tts  # Will break other cells, but necessary to conserve RAM if you want to run this cell.

# Tortoise comes with some scripts that does a lot of the lifting for you. For example,
# read.py will read a text file for you.
!python3 tortoise/read.py --voice=mk --textfile=text_to_read.txt --preset=high_quality --output_path=text_read.wav

IPython.display.Audio('text_read.wav')
# This will take awhile..

NameError: ignored

In [ ]:

IPython.display.Audio('train_atkins/combined.wav')